In [41]:
import pandas as pd
import movingpandas as mpd

import warnings
warnings.filterwarnings('ignore')

In [42]:
df = pd.read_csv("ankle_monitor/JaredCombs_Ankle_Monitor.csv")

In [43]:
df.head(2)

datetime  location_x  location_y firstname lastname  \
0  2016-11-07T00:00:10.000-05:00  -76.658023   39.286675     Jared    Combs   
1  2016-11-07T00:00:20.000-05:00  -76.658099   39.286706     Jared    Combs   

  middlename          ssn  
0     Skyler  901-NI-6283  
1     Skyler  901-NI-6283

In [44]:
df.dtypes

datetime       object
location_x    float64
location_y    float64
firstname      object
lastname       object
middlename     object
ssn            object
dtype: object

In [45]:
df['datetime'] = pd.to_datetime(df['datetime'])

In [6]:
df.shape

(43057, 7)

In [7]:
df['datetime'].min(), df['datetime'].max()

(Timestamp('2016-11-07 00:00:10-0500', tz='pytz.FixedOffset(-300)'),
 Timestamp('2016-11-11 23:59:57-0500', tz='pytz.FixedOffset(-300)'))

In [8]:
df = df[df['datetime'] < '2016-11-08']

In [46]:
traj = mpd.Trajectory(df, "SCombs", t="datetime", x="location_x", y="location_y", crs=4326)

In [11]:
traj.df

firstname lastname middlename          ssn  \
datetime                                                         
2016-11-07 00:00:10     Jared    Combs     Skyler  901-NI-6283   
2016-11-07 00:00:20     Jared    Combs     Skyler  901-NI-6283   
2016-11-07 00:00:30     Jared    Combs     Skyler  901-NI-6283   
2016-11-07 00:00:40     Jared    Combs     Skyler  901-NI-6283   
2016-11-07 00:00:50     Jared    Combs     Skyler  901-NI-6283   
...                       ...      ...        ...          ...   
2016-11-07 23:59:12     Jared    Combs     Skyler  901-NI-6283   
2016-11-07 23:59:22     Jared    Combs     Skyler  901-NI-6283   
2016-11-07 23:59:32     Jared    Combs     Skyler  901-NI-6283   
2016-11-07 23:59:42     Jared    Combs     Skyler  901-NI-6283   
2016-11-07 23:59:52     Jared    Combs     Skyler  901-NI-6283   

                                       geometry  
datetime                                         
2016-11-07 00:00:10  POINT (-76.65802 39.28668)  
2016-11-07 00:00:20  POINT (-76.65810 39.28671)  
2016-11-07 00:00:30  POINT (-76.65804 39.28670)  
2016-11-07 00:00:40  POINT (-76.65790 39.28670)  
2016-11-07 00:00:50  POINT (-76.65796 39.28678)  
...                                         ...  
2016-11-07 23:59:12  POINT (-76.65791 39.28674)  
2016-11-07 23:59:22  POINT (-76.65801 39.28682)  
2016-11-07 23:59:32  POINT (-76.65800 39.28670)  
2016-11-07 23:59:42  POINT (-76.65806 39.28669)  
2016-11-07 23:59:52  POINT (-76.65801 39.28671)  

[8603 rows x 5 columns]

In [12]:
traj.hvplot(c='speed', line_width=4, colorbar=True)

:Overlay
   .Tiles.I :Tiles   [x,y]
   .Path.I  :Path   [Longitude,Latitude]   (speed)

In [13]:
from datetime import timedelta

In [15]:
detector = mpd.TrajectoryStopDetector(traj)

In [17]:
stops = detector.get_stop_points(min_duration=timedelta(seconds=600), max_diameter=50)

In [18]:
stops

geometry          start_time  \
stop_id                                                                      
SCombs_2016-11-07 00:00:10  POINT (-76.65802 39.28668) 2016-11-07 00:00:10   
SCombs_2016-11-07 10:10:23  POINT (-76.66487 39.29684) 2016-11-07 10:10:23   
SCombs_2016-11-07 10:38:59  POINT (-76.65997 39.29512) 2016-11-07 10:38:59   
SCombs_2016-11-07 11:07:48  POINT (-76.65829 39.28656) 2016-11-07 11:07:48   
SCombs_2016-11-07 12:43:20  POINT (-76.65359 39.28431) 2016-11-07 12:43:20   
SCombs_2016-11-07 13:49:40  POINT (-76.65770 39.28668) 2016-11-07 13:49:40   

                                      end_time traj_id  duration_s  
stop_id                                                             
SCombs_2016-11-07 00:00:10 2016-11-07 09:53:09  SCombs     35579.0  
SCombs_2016-11-07 10:10:23 2016-11-07 10:30:00  SCombs      1177.0  
SCombs_2016-11-07 10:38:59 2016-11-07 10:52:13  SCombs       794.0  
SCombs_2016-11-07 11:07:48 2016-11-07 12:25:51  SCombs      4683.0  
SCombs_2016-11-07 12:43:20 2016-11-07 13:41:47  SCombs      3507.0  
SCombs_2016-11-07 13:49:40 2016-11-07 23:59:52  SCombs     36612.0

In [20]:
stops = stops.set_crs(4326)

In [21]:
import hvplot.pandas

In [25]:
stops.hvplot(geo=True, tiles=True, hover_cols="all", frame_height=300, frame_width=300) + \
traj.hvplot(geo=True, tiles=True, hover_cols="all", frame_height=300, frame_width=300)

:Layout
   .Overlay.I  :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]   (stop_id,start_time,end_time,traj_id,duration_s)
   .Overlay.II :Overlay
      .Tiles.I :Tiles   [x,y]
      .Path.I  :Path   [Longitude,Latitude]   (datetime,firstname,lastname,middlename,ssn,t,prev_t)

In [27]:
traj_col = mpd.StopSplitter(traj).split(max_diameter=50, min_duration=timedelta(seconds=600))

In [28]:
traj_col.hvplot(line_width=3)

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Path.I   :Path   [Longitude,Latitude]
   .Path.II  :Path   [Longitude,Latitude]
   .Path.III :Path   [Longitude,Latitude]
   .Path.IV  :Path   [Longitude,Latitude]
   .Path.V   :Path   [Longitude,Latitude]

In [47]:
import geopandas as gpd

In [48]:
crimes = gpd.read_file("CrimeLaydown.shp")

In [49]:
crimes

lat        lon                  dtg  \
0   39.291796 -76.648672   11/07/2016 2:31 PM   
1   39.287518 -76.643107  11/07/2016 12:00 PM   
2   39.283933 -76.651033   11/07/2016 8:14 PM   
3   39.288788 -76.646520   11/07/2016 5:15 AM   
4   39.288080 -76.652325   11/07/2016 3:25 PM   
..        ...        ...                  ...   
79  39.298172 -76.665271  11/11/2016 10:30 AM   
80  39.295419 -76.653435  11/11/2016 12:58 PM   
81  39.304904 -76.669310  11/11/2016 11:59 AM   
82  39.286013 -76.672746  11/11/2016 11:32 AM   
83  39.297920 -76.664757   11/11/2016 7:24 AM   

                                                 text  \
0   On 11/07/2016 at approximately 2:31 PM, office...   
1   The Baltimore Police Department is announcing ...   
2   The Baltimore Police Department responded to r...   
3   The Baltimore Police Department is seeking the...   
4   Baltimore police are seeking information in co...   
..                                                ...   
79  Baltimore Police are seeking the public?s help...   
80  The Baltimore Police Department is seeking the...   
81  The Baltimore Police Department is seeking the...   
82  The Baltimore Police Department is seeking the...   
83  The Baltimore Police Department is seeking the...   

                      geometry  
0   POINT (-76.64867 39.29180)  
1   POINT (-76.64311 39.28752)  
2   POINT (-76.65103 39.28393)  
3   POINT (-76.64652 39.28879)  
4   POINT (-76.65233 39.28808)  
..                         ...  
79  POINT (-76.66527 39.29817)  
80  POINT (-76.65344 39.29542)  
81  POINT (-76.66931 39.30490)  
82  POINT (-76.67275 39.28601)  
83  POINT (-76.66476 39.29792)  

[84 rows x 5 columns]

In [50]:
from pyproj import CRS

In [51]:
traj = traj.to_crs(CRS(3857))

In [52]:
crimes = crimes.to_crs(3857)

In [53]:
crimes['dt'] = pd.to_datetime(crimes['dtg'])

In [36]:
crimes = crimes[crimes['dt'] < '2016-11-08']

In [37]:
crimes

lat        lon                  dtg  \
0   39.291796 -76.648672   11/07/2016 2:31 PM   
1   39.287518 -76.643107  11/07/2016 12:00 PM   
2   39.283933 -76.651033   11/07/2016 8:14 PM   
3   39.288788 -76.646520   11/07/2016 5:15 AM   
4   39.288080 -76.652325   11/07/2016 3:25 PM   
5   39.282070 -76.668267   11/07/2016 4:03 AM   
6   39.285406 -76.680225   11/07/2016 6:54 AM   
7   39.285224 -76.676606   11/07/2016 4:44 AM   
8   39.285332 -76.646281   11/07/2016 9:16 AM   
9   39.268469 -76.649393   11/07/2016 7:26 AM   
10  39.279580 -76.654728   11/07/2016 5:34 AM   
11  39.298184 -76.656653   11/07/2016 7:00 PM   
12  39.284218 -76.653295   11/07/2016 8:24 PM   
13  39.296990 -76.664850  11/07/2016 10:30 AM   
14  39.292006 -76.642998   11/07/2016 1:40 PM   
15  39.297078 -76.648476   11/07/2016 3:07 PM   

                                                 text  \
0   On 11/07/2016 at approximately 2:31 PM, office...   
1   The Baltimore Police Department is announcing ...   
2   The Baltimore Police Department responded to r...   
3   The Baltimore Police Department is seeking the...   
4   Baltimore police are seeking information in co...   
5   Baltimore Police have arrested Karen Mikkelson...   
6   Baltimore Police officers were patrolling arou...   
7   On 11/07/2016, bicycle officers were on patrol...   
8   On 11/07/2016, bicycle officers on patrol when...   
9   Baltimore police officers were patrolling arou...   
10  Baltimore Police officers were patrolling past...   
11  On 11/07/2016, bike officers were on patrol ne...   
12  The Baltimore Police Department is investigati...   
13  Baltimore Police are investigating a robbery t...   
14  The Baltimore Police Department arrested Carme...   
15  The Baltimore Police Department is seeking the...   

                            geometry                  dt  
0   POINT (-8532491.137 4763555.453) 2016-11-07 14:31:00  
1   POINT (-8531871.644 4762940.139) 2016-11-07 12:00:00  
2   POINT (-8532753.962 4762424.530) 2016-11-07 20:14:00  
3   POINT (-8532251.577 4763122.802) 2016-11-07 05:15:00  
4   POINT (-8532897.787 4763020.970) 2016-11-07 15:25:00  
5   POINT (-8534672.442 4762156.596) 2016-11-07 04:03:00  
6   POINT (-8536003.601 4762636.379) 2016-11-07 06:54:00  
7   POINT (-8535600.736 4762610.204) 2016-11-07 04:44:00  
8   POINT (-8532224.972 4762625.737) 2016-11-07 09:16:00  
9   POINT (-8532571.398 4760200.738) 2016-11-07 07:26:00  
10  POINT (-8533165.288 4761798.499) 2016-11-07 05:34:00  
11  POINT (-8533379.578 4764474.322) 2016-11-07 19:00:00  
12  POINT (-8533005.767 4762465.519) 2016-11-07 20:24:00  
13  POINT (-8534292.064 4764302.567) 2016-11-07 10:30:00  
14  POINT (-8531859.510 4763585.658) 2016-11-07 13:40:00  
15  POINT (-8532469.318 4764315.226) 2016-11-07 15:07:00

In [56]:
crimes['sus_loc'] = crimes['dt'].apply(traj.get_position_at)

In [58]:
crimes['distance'] = crimes.apply(lambda row: row['geometry'].distance(row['sus_loc']), axis=1)

In [59]:
crimes[crimes['distance'] < 200]

lat        lon                  dtg  \
13  39.296990 -76.664850  11/07/2016 10:30 AM   
56  39.285439 -76.658475   11/10/2016 5:07 PM   

                                                 text  \
13  Baltimore Police are investigating a robbery t...   
56  The Baltimore Police Department responded to r...   

                            geometry                  dt  \
13  POINT (-8534292.064 4764302.567) 2016-11-07 10:30:00   
56  POINT (-8533582.402 4762641.126) 2016-11-10 17:07:00   

                                         sus_loc    distance  
13   POINT (-8534294.809431603 4764261.05116728)   41.606483  
56  POINT (-8533532.916456401 4762829.824183024)  195.079368

In [66]:
stops.hvplot(geo=True, tiles=True, frame_height=400, frame_width=400) + \
crimes[crimes['distance'] < 200].hvplot(tiles=True, frame_height=400, frame_width=400)

:Layout
   .Overlay.I  :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [Longitude,Latitude]
   .Overlay.II :Overlay
      .Tiles.I  :Tiles   [x,y]
      .Points.I :Points   [x,y]